<a href="https://colab.research.google.com/github/anjunjin/PFE-ING3-IA/blob/branch1/ScatterText.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
from google.colab import drive

drive.mount('/content/drive')
DATA_PATH = "/content/drive/My Drive/PFE/"
df_group = pd.read_csv(DATA_PATH+"Tweets_nettoyés_040222.csv", encoding='utf-8').drop(['Unnamed: 0'], axis=1)

Mounted at /content/drive


/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2882: DtypeWarning: Columns (0,1) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


On effectue l'annalyse sur seulement 20 000 tweets, réduisant les ressources nécessaires mais conservant la proportion d'apparition des différents labels des tweets

In [2]:
df_group = df_group.sample(n=20000, replace=False, random_state=42)
df_group

liability  ...                                            cleaned
603868         1  ...  🟥ratpgrève aujourd’hui desident_number lignes ...
217747         0  ...  regenerons covid19 antibody drug may be less e...
554624         1  ...     is trump sanctioning the sky now desident_link
717363         0  ...  rt déboisement déforestation désastre planétai...
453151         0  ...  flûte faisait comprendre enchantait royaume cé...
...          ...  ...                                                ...
103625         0  ...  contenu loi « sécurité globale » alexis toulet...
90873          0  ...  président burkinabé conteste manque respect bl...
136159         0  ...  desident_number  minute beauté mise pantalon c...
247927         0  ...  black friday sélection lego stylés enfants 👇de...
38156          1  ...  moment charles michel annoncé démission vidéo ...

[20000 rows x 9 columns]

In [3]:
!pip install scattertext

     |████████████████████████████████| 7.3 MB 5.0 MB/s 
     |████████████████████████████████| 24.1 MB 1.8 MB/s 
  Created wheel for flashtext: filename=flashtext-2.7-py2.py3-none-any.whl size=9309 sha256=ed684f4f1df2759b2dfe537f654729173917cb88f75491237a05ad9475905c9c
  Stored in directory: /root/.cache/pip/wheels/cb/19/58/4e8fdd0009a7f89dbce3c18fff2e0d0fa201d5cdfd16f113b7
Successfully built flashtext
  Attempting uninstall: gensim
    Found existing installation: gensim 3.6.0
    Uninstalling gensim-3.6.0:
      Successfully uninstalled gensim-3.6.0


In [4]:
import scattertext as st
import spacy
from spacy.tokenizer import Tokenizer
from spacy.lang.fr import French
import numpy as np
import math

In [5]:
spacy.cli.download('fr_core_news_md')

✔ Download and installation successful
You can now load the model via spacy.load('fr_core_news_md')


In [6]:
nlp = spacy.load("fr_core_news_md")

In [7]:
"""c= 0 
for sentence in df_group['cleaned']:
  if not isinstance(sentence, str):
    df_group = df_group.drop(labels=[c], axis=0) 

  c = c+1"""

"c= 0 \nfor sentence in df_group['cleaned']:\n  if not isinstance(sentence, str):\n    df_group = df_group.drop(labels=[c], axis=0) \n\n  c = c+1"

In [8]:
df_group = df_group.reset_index(drop=True)
df_group = df_group.dropna()
# df_group.loc[df_group["cleaned"].str.contains("NaN"), ["cleaned","tweet","user_screen_name","liability_label"]] #.sample(25, replace=False)
# df_group = df_group.drop(df_group[df_group.index.isin([35203, 35220, 111663, 111664, 111665, 111666, 111667, 142467, 247758, 249448, 458701, 545318, 545319, 548835, 549118, 550069, 584385, 584386, 584387, 596245, 596709, 596779, 634646, 663672, 663701, 663706, 700933])].index)
len("test")
df_group.sort_values(by = 'cleaned')

liability  ...                                            cleaned
3909          0  ...    résistance futile ➡️ desident_link partait r...
14488         0  ...    walle ➡️ desident_link regard dun petit robo...
11654         0  ...   adopte définition lantisémitisme lihra deside...
5924          0  ...   ans prison ferme revendu cigarettes contrefaç...
8809          0  ...   ans standard ’argent aujourd’hui cherche desi...
...         ...  ...                                                ...
1064          1  ...                                    󾌧 desident_link
3021          1  ...                                    󾍁 desident_link
16350         1  ...              󾍁󾍁󾍁 cest panique totale desident_link
9596          1  ...                                  󾍁󾍁󾍁 desident_link
16537         1  ...                                  󾍁󾍁󾍁 desident_link

[19976 rows x 9 columns]

In [9]:
df_group.loc[df_group["cleaned"].str.contains("rt 🔴"), ["cleaned","tweet","user_screen_name","liability_label"]] #.sample(25, replace=False)

cleaned  ...      liability_label
59     rt 🔴 tuerie traitement médiatique ’est rappele...  ...  site plutôt douteux
179    rt 🔴 urgent présidentielle desident_date yanni...  ...   site plutôt fiable
229    rt 🔴 envie commencer journée bonne humeur marm...  ...   site plutôt fiable
871    rt 🔴 violences policières – desident_number er...  ...   site plutôt fiable
1059   rt 🔴miss france ministre elisabeth moreno juge...  ...  site plutôt douteux
...                                                  ...  ...                  ...
18733  rt 🔴 calendrier lavent bb cest évidemment meil...  ...   site plutôt fiable
18765  rt 🔴 thread cest cest important bb cest deside...  ...   site plutôt fiable
18783  rt 🔴 sujets jour quotidienne desident_number ⃣...  ...   site plutôt fiable
19333  rt 🔴 desident_number nd guerre montre  chance ...  ...   site plutôt fiable
19909  rt 🔴 “il menaçait décapiter” individu suspecté...  ...  site plutôt douteux

[82 rows x 4 columns]

In [10]:
# parse speech text using spaCy
df_group['parsed'] = df_group.cleaned.apply(nlp)

In [11]:
# convert dataframe into Scattertext corpus
corpus_group = st.CorpusFromParsedDocuments(df_group, category_col='liability_label', parsed_col='parsed').build()

In [12]:
df_group.loc[df_group["cleaned"].str.contains(r"\b(gt)+"), ["cleaned","tweet","user_screen_name","liability_label"]] #.sample(25, replace=False)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  """Entry point for launching an IPython kernel.


Empty DataFrame
Columns: [cleaned, tweet, user_screen_name, liability_label]
Index: []

In [13]:
df_group.loc[df_group["cleaned"].str.contains(r"\b[a-zA-Z]\b"), ["cleaned","tweet","user_screen_name","liability_label"]] #.sample(25, replace=False)

Empty DataFrame
Columns: [cleaned, tweet, user_screen_name, liability_label]
Index: []

In [14]:
import IPython

# visualize term associations
html = st.produce_scattertext_explorer(corpus_group,
                                    category='site plutôt fiable',
                                    category_name='site plutôt fiable',
                                    not_category_name='site plutôt douteux',
                                    width_in_pixels=1000,
                                    minimum_term_frequency=5,
                                    transform=st.Scalers.dense_rank #st.Scalers.percentile_ordinal ou st.Scalers.scale(vect) ou st.Scalers.dense_rank
                                    )

"""with open(DATA_PATH+"scatter_text.html", "wb") as file_html:
  file_html.write(html.encode('utf-8'))"""

# open(DATA_PATH+"Scattertext.html", 'wb').write(html.encode('utf-8'))

file_name = 'Scattertext_040222.html'
open(DATA_PATH+file_name, 'wb').write(html.encode('utf-8'))
IPython.display.HTML(filename=DATA_PATH+file_name)

In [15]:
open(DATA_PATH+"Scattertext_040222.html", 'wb').write(html.encode('utf-8'))

3741241

In [16]:
df_group.to_csv('Tweets_parsed_040222.csv')
!cp Tweets_parsed_040222.csv "/content/drive/My Drive/PFE"